In [1]:
# load packages
import requests
from bs4 import BeautifulSoup
from time import sleep
import csv
from datetime import datetime
import pandas as pd
import random
import json

In [2]:
# empty lists
urls = []
all_music = []
data = []
all_data = []

In [3]:
url = 'https://www.tunefind.com/browse/tv'

In [4]:
# gather urls
response = requests.get(url)
soup = BeautifulSoup(response.text, "html.parser")
musicmachine = soup.find_all(class_="GroupedList_item__CRZnU")
for soup in musicmachine:
    my_music = {}
    
    if soup.find('a', href=True) == None: 
        pass
    else:
        link = soup.find('a', href=True)
        if link['href'].startswith('/show'):
            link = 'https://www.tunefind.com' + link['href']
            my_music['link'] = link
            sleep(3)
    urls.append(my_music)

In [5]:
# gather first page info
for my_music in urls:
    response = requests.get(my_music['link'])
    soup = BeautifulSoup(response.text, "html.parser")
    full_page = soup.find_all(class_="EpisodeListItem_container__dhZur")
    music = {}
    
    if soup.find(class_="TvHeader_title__z0y6G") == None: 
        pass
    else:
        title = soup.find(class_="TvHeader_title__z0y6G").text
        music['title'] = title

    for soup in full_page:
        if soup.find(class_="EpisodeListItem_title__PkSzj") == None: 
            pass
        else:
            season = soup.find(class_="EpisodeListItem_title__PkSzj").text
            music['season'] = season
            
        if soup.find(class_="EpisodeListItem_subtitle__cupzX") == None:
            pass
        else:
            date = soup.find(class_="EpisodeListItem_subtitle__cupzX").text
            music['date'] = date
            
        if soup.find('a', href=True) == None: 
            pass
        else:
            link_season = soup.find('a', href=True)
            if link_season['href'].startswith('/show'):
                link_season = "https://www.tunefind.com" + link_season['href']
                music['link_season'] = link_season
        sleep(3)
        all_music.append(music.copy())

In [6]:
# define function that retrieves episode info
def retrieve_episode_page_info(soup):
    card = {}
    if soup.find(class_="EpisodeListItem_title__PkSzj") == None:
        card['episode'] = None
    else:
        episode = soup.find(class_="EpisodeListItem_title__PkSzj").text
        card['episode'] = episode

    if soup.find(class_="EpisodeListItem_subtitle__cupzX") == None:
        card['releasedate_episode'] = None
    else:
        releasedate_episode = soup.find(class_="EpisodeListItem_subtitle__cupzX").text
        card['releasedate_episode'] = releasedate_episode

    if soup.find(class_="EpisodeListItem_description__VxFAI") == None:
        card['episode_description'] = None
    else:
        episode_description = soup.find(class_="EpisodeListItem_description__VxFAI").text
        card['episode_description'] = episode_description

    if soup.find('a', href=True) == None:
        card['link_episode'] = None
    else:
        link_episode = soup.find('a', href=True)
        if link_episode['href'].startswith('/show'):
            link_episode = "https://www.tunefind.com" + link_episode['href']
            card['link_episode'] = link_episode
        else:
            card['link_episode'] = None
    return card

In [7]:
# gather second page info
i = 1
for music in all_music:
    #Get page info
    req = requests.get(music['link_season'])
    soup = BeautifulSoup(req.text, "html.parser")
    full_page_2 = soup.find_all(class_="MainList_item__bR_g9")
    print(f"{i}/{len(all_music)} Looking at {music['link_season']}")
    i += 1
    #Loop over episodes on page
    for soup in full_page_2:
        #retrieve episode data
        episode_info = retrieve_episode_page_info(soup)
        #Add season data
        episode_info['link_season'] = music['link_season']
        episode_info['date'] = music['date']
        episode_info['season'] = music['season']
        episode_info['title'] = music['title']
        
        sleep(2)
        print(episode_info['episode'])
        #Title is none when e.g. ad. Only add info if episode
        if episode_info['episode'] != None:
            data.append(episode_info)

1/8131 Looking at https://www.tunefind.com/show/blackaf/season-1
S1 · E1 · because of slavery
S1 · E2 · because of slavery too
None
S1 · E3 · still... because of slavery
S1 · E4 · yup, you guessed it. again, this is because of slavery
None
S1 · E5 · yo, between you and me... this is because of slavery
S1 · E6 · hard to believe, but still because of slavery
S1 · E7 · i know this is going to sound crazy... but this, too, is because of slavery
S1 · E8 · i know you may not get this, but the reason we deserve a vacation is... because of slavery
2/8131 Looking at https://www.tunefind.com/show/112263/season-1
S1 · E1 · The Rabbit Hole
S1 · E2 · The Kill Floor
None
S1 · E3 · Other Voices, Other Rooms
S1 · E4 · The Eyes of Texas
None
S1 · E5 · The Truth
S1 · E6 · Happy Birthday, Lee Harvey Oswald
S1 · E7 · Soldier Boy
S1 · E8 · The Day in Question
3/8131 Looking at https://www.tunefind.com/show/12-dates-of-christmas/season-1
S1 · E1 · Meet, Sleigh, Love
S1 · E2 · Tis the Season to be Naughty
No

S3 · E14 · And The Dumpster Sex
S3 · E15 · And The Icing On The Cake
S3 · E16 · And the ATM
S3 · E17 · And the Married Man Sleepover
None
S3 · E18 · And The Near Death Experience
S3 · E19 · And the Kilt Trip
S3 · E20 · And the Not Broke Parents
S3 · E21 · And the Wedding Cake Cake Cake
S3 · E22 · And The New Lease On Life
S3 · E23 · And the Free Money
S3 · E24 · And The First Degree
19/8131 Looking at https://www.tunefind.com/show/2-broke-girls/season-4
S4 · E1 · And the Reality Problem
S4 · E2 · And the DJ Face
None
S4 · E3 · And the Childhood Not Included
S4 · E4 · And the Old Bike Yarn
None
S4 · E5 · And the Brand Job
S4 · E6 · And the Model Apartment
S4 · E7 · And a Loan for Christmas
None
S4 · E8 · And the Fun Factory
S4 · E9 · And the Past and the Furious
S4 · E10 · And the Move-In Meltdown
S4 · E11 · And the Crime Ring
S4 · E12 · And the Knock Off Knockout
S4 · E13 · And the Great Unwashed
S4 · E14 · And the Cupcake Captives
S4 · E15 · And the Fat Cat
S4 · E16 · And the Zero Tol

S2 · E7 · Day 2: 2:00 P.M. - 3:00 P.M.
None
S2 · E8 · Day 2: 3:00 P.M. - 4:00 P.M.
S2 · E9 · Day 2: 4:00 P.M. - 5:00 P.M.
S2 · E10 · Day 2: 5:00 P.M. - 6:00 P.M.
S2 · E11 · Day 2: 6:00 P.M. - 7:00 P.M.
S2 · E12 · Day 2: 7:00 P.M. - 8:00 P.M.
S2 · E13 · Day 2: 8:00 P.M. - 9:00 P.M.
S2 · E14 · Day 2: 9:00 P.M. - 10:00 P.M.
S2 · E15 · Day 2: 10:00 P.M. - 11:00 P.M.
S2 · E16 · Day 2: 11:00 P.M. - 12:00 A.M.
S2 · E17 · Day 2: 12:00 A.M. - 1:00 A.M.
None
S2 · E18 · Day 2: 1:00 A.M. - 2:00 A.M.
S2 · E19 · Day 2: 2:00 A.M. - 3:00 A.M.
S2 · E20 · Day 2: 3:00 A.M. - 4:00 A.M.
S2 · E21 · Day 2: 4:00 A.M. - 5:00 A.M.
S2 · E22 · Day 2: 5:00 A.M. - 6:00 A.M.
S2 · E23 · Day 2: 6:00 A.M. - 7:00 A.M.
S2 · E24 · Day 2: 7:00 A.M. - 8:00 A.M.
32/8131 Looking at https://www.tunefind.com/show/24/season-3
S3 · E1 · Day 3: 1:00 P.M. - 2:00 P.M.
S3 · E2 · Day 3: 2:00 P.M. - 3:00 P.M.
None
S3 · E3 · Day 3: 3:00 P.M. - 4:00 P.M.
S3 · E4 · Day 3: 4:00 P.M. - 5:00 P.M.
None
S3 · E5 · Day 3: 5:00 P.M. - 6:00 P.M.
S

None
S1 · E5 · Chapter 05: Water
S1 · E6 · Chapter 06: Glass
S1 · E7 · Chapter 07: Capsule
S1 · E8 · Chapter 08: Button
41/8131 Looking at https://www.tunefind.com/show/3/season-2
S2 · E1 · Chapter 01: Mirror
S2 · E2 · Chapter 02: Toaster
None
S2 · E3 · Chapter 03: Static
S2 · E4 · Chapter 04: Napkin
None
S2 · E5 · Chapter 05: Lamp
S2 · E6 · Chapter 06: Bottles
S2 · E7 · Chapter 07: Fog
None
S2 · E8 · Chapter 08: Frogs
S2 · E9 · Chapter 09: Necklace
S2 · E10 · Chapter 10: Blood
42/8131 Looking at https://www.tunefind.com/show/3/season-3
S3 · E1 · Chapter 01: Sand
S3 · E2 · Chapter 02: Scalpel
None
S3 · E3 · Chapter 03: Medicine
S3 · E4 · Chapter 04: Duck
None
S3 · E5 · Chapter 05: Lever
S3 · E6 · Chapter 06: Trapdoor
S3 · E7 · Chapter 07: Gardrone
S3 · E8 · Chapter 08: Wave
43/8131 Looking at https://www.tunefind.com/show/3/season-4
S4 · E1 · Chapter 01: Moon
S4 · E2 · Chapter 02: Shock
None
S4 · E3 · Chapter 03: Fire
S4 · E4 · Chapter 04: Submarine
None
S4 · E5 · Chapter 05: Painting


None
S6 · E5 · Today You Are a Man
S6 · E6 · Hey, Baby, What's Wrong (1)
S6 · E7 · Hey, Baby, What's Wrong (2)
None
S6 · E8 · The Tuxedo Begins
S6 · E9 · Leap Day
S6 · E10 · Alexis Goodlooking and the Case of the Missing Whisky
S6 · E11 · Standards and Practises
S6 · E12 · St. Patrick's Day
S6 · E13 · Grandmentor
S6 · E14 · Kidnapped by Danger
S6 · E15 · The Shower Principle
S6 · E16 · Nothing Left to Lose
S6 · E17 · Meet the Woggels
None
S6 · E18 · Murphy Brown Lied to Us
S6 · E19 · Live from Studio 6H
S6 · E20 · Queen of Jordan 2: The Mystery of the Phantom Pooper
S6 · E21 · The Return of Avery Jessup
S6 · E22 · What Will Happen to the Gang Next Year?
55/8131 Looking at https://www.tunefind.com/show/30-rock/season-7
S7 · E1 · The Beginning of the End
S7 · E2 · Governor Dunston
None
S7 · E3 · Stride of Pride
S7 · E4 · Unwindulax
None
S7 · E5 · There's No I in America
S7 · E6 · Aunt Phatso vs. Jack Donaghy
S7 · E7 · Mazel Tov, Dummies!
None
S7 · E8 · My Whole Life Is Thunder
S7 · E9 · 

...

S3 · E6 · Het ging allemaal focking snel.
S3 · E7 · Ik heb het verpest. Ik weet het.
None
S3 · E8 · Zo rap ben je van mij nog niet af.
S3 · E9 · Je bent gewoon zijn volgende obsessie.
S3 · E10 · Ander onderwerp. Oké?
8047/8131 Looking at https://www.tunefind.com/show/wtfock/season-4
S4 · E1 · Focking kutvirus.
S4 · E2 · Die Moyo heeft wel iets.
None
S4 · E3 · Nobody puts baby Kato in the corner.
S4 · E4 · Wat een schmett.
None
S4 · E5 · Get the fock out.
S4 · E6 · Ze zijn er echt over gegaan.
S4 · E7 · Alles vor de liefde.
None
S4 · E8 · Niemand luistert echt naar mij.
S4 · E9 · Ik denk niet dat dat zo slim is.
S4 · E10 · Sommige shit veroorzaakt ge zelf.
8048/8131 Looking at https://www.tunefind.com/show/wtfock/season-5
S5 · E1 · Episode 1
S5 · E2 · Episode 2
None
S5 · E3 · Episode 3
S5 · E4 · Episode 4
None
S5 · E5 · Episode 5
S5 · E6 · Episode 6
S5 · E7 · Episode 7
None
S5 · E8 · Episode 8
S5 · E9 · Episode 9
S5 · E10 · Episode 10
8049/8131 Looking at https://www.tunefind.com/show/w

None
S1 · E3 · Maybe
S1 · E4 · The Captain
None
S1 · E5 · Living with the Enemy
S1 · E6 · Amour Fou
S1 · E7 · Everythingship
None
S1 · E8 · You Got Me Babe
S1 · E9 · Candace
S1 · E10 · Bluebeard's Castle
8070/8131 Looking at https://www.tunefind.com/show/you/season-2
S2 · E1 · A Fresh Start
S2 · E2 · Just the Tip
None
S2 · E3 · What Are Friends For?
S2 · E4 · The Good, the Bad, & the Hendy
None
S2 · E5 · Have a Good Wellkend, Joe!
S2 · E6 · Farewell, My Bunny
S2 · E7 · Ex-istential Crisis
None
S2 · E8 · Fear and Loathing in Beverly Hills
S2 · E9 · P.I. Joe
S2 · E10 · Love, Actually
8071/8131 Looking at https://www.tunefind.com/show/you/season-3
S3 · E1 · And They Lived Happily Ever After
S3 · E2 · So I Married an Axe Murderer
None
S3 · E3 · Missing White Woman Syndrome
S3 · E4 · Hands Across Madre Linda
None
S3 · E5 · Into the Woods
S3 · E6 · W.O.M.B.
S3 · E7 · We're All Mad Here
None
S3 · E8 · Swing and a Miss
S3 · E9 · Red Flag
S3 · E10 · What Is Love?
8072/8131 Looking at https://ww

S4 · E9 · Young & Matched
S4 · E10 · Young & Screwed
8089/8131 Looking at https://www.tunefind.com/show/young-hungry/season-5
S5 · E1 · Young & Punch Card
S5 · E2 · Young & Valentine's Day
None
S5 · E3 · Young & Kiki
S5 · E4 · Young & Josh's Dad
None
S5 · E5 · Young & Softball
S5 · E6 · Young & Couchy
S5 · E7 · Young & Bridesmaids
None
S5 · E8 · Young & Vegas Baby
S5 · E9 · Young & Hold
S5 · E10 · Young & Amnesia
8090/8131 Looking at https://www.tunefind.com/show/young-rock/season-1
S1 · E1 · Working the Gimmick
S1 · E2 · On the Road Again
None
S1 · E3 · Forward, Together
S1 · E4 · Check Your Head
None
S1 · E5 · Don't Go Breaking My Heart
S1 · E6 · My Day with Andre
S1 · E7 · Johnson & Hopkins
None
S1 · E8 · My Baby Only Drinks the Good Stuff
S1 · E9 · A Lady Named Star Search
S1 · E10 · Good vs. Great
S1 · E11 · Election Day
8091/8131 Looking at https://www.tunefind.com/show/young-rock/season-2
S2 · Special · A Christmas Peril
S2 · E1 · Unprecedented Fatherhood
None
S2 · E2 · Seven Bu

S2 · E6 · Avsnitt 6
8101/8131 Looking at https://www.tunefind.com/show/younger/season-1
S1 · E1 · Pilot
S1 · E2 · Liza Sows Her Oates
None
S1 · E3 · IRL
S1 · E4 · The Exes
None
S1 · E5 · Girl Code
S1 · E6 · Shedonism
S1 · E7 · Broke and Pantyless
None
S1 · E8 · Sk8
S1 · E9 · I'm With Stupid
S1 · E10 · The Boy With the Dragon Tattoo
S1 · E11 · Hot Mitzvah
S1 · E12 · The Old Ma'am and the C
8102/8131 Looking at https://www.tunefind.com/show/younger/season-2
S2 · Special · Sneak Peek
S2 · E1 · Tattoo You
None
S2 · E2 · The Mao Function
S2 · E3 · Like a Boss
None
S2 · E4 · The Jade Crusade
S2 · E5 · Jersey, Sure
S2 · E6 · Un-Jaded
None
S2 · E7 · Into the Woods and Out of the Woods
S2 · E8 · Beyond Therapy
S2 · E9 · The Good Shepherd
S2 · E10 · Bad Romance
S2 · E11 · Secrets & Liza
S2 · E12 · No Weddings & A Funeral
8103/8131 Looking at https://www.tunefind.com/show/younger/season-3
S3 · E1 · A Kiss is Just A Kiss
S3 · E2 · The Marshmallow Experiment
None
S3 · E3 · Last Days of Books
S3 · E

S1 · E6 · Head Rush
S1 · E7 · Triple Threat
None
S1 · E8 · Guilt Trip
S1 · E9 · This Is Happening
S1 · E10 · Blade Star
8123/8131 Looking at https://www.tunefind.com/show/zerozerozero/season-1
S1 · E1 · Il carico
S1 · E2 · I cieli su Tampico
None
S1 · E3 · Miranda
S1 · E4 · Il trasbordo
None
S1 · E5 · Sharia
S1 · E6 · Salvezza
S1 · E7 · Famiglia
S1 · E8 · Stesso sangue
8124/8131 Looking at https://www.tunefind.com/show/zoeys-extraordinary-playlist/season-1
S1 · E1 · Pilot
S1 · E2 · Zoey's Extraordinary Best Friend
None
S1 · E3 · Zoey's Extraordinary Boss
S1 · E4 · Zoey's Extraordinary Neighbor
None
S1 · E5 · Zoey's Extraordinary Failure
S1 · E6 · Zoey's Extraordinary Night Out
S1 · E7 · Zoey's Extraordinary Confession
None
S1 · E8 · Zoey's Extraordinary Glitch
S1 · E9 · Zoey's Extraordinary Silence
S1 · E10 · Zoey's Extraordinary Outburst
S1 · E11 · Zoey's Extraordinary Mother
S1 · E12 · Zoey's Extraordinary Dad
8125/8131 Looking at https://www.tunefind.com/show/zoeys-extraordinary-pla

In [8]:
# print to csv
df = pd.DataFrame(data)
df.to_csv('tunefind_data_episode.csv', sep=";")

In [9]:
# define function that retrieves song info
def retrieve_song_page_info(soup):
    song = {}
    if soup.find(class_="SongTitle_link__qlRUV") == None: 
        pass
    else:
        song_title = soup.find(class_="SongTitle_link__qlRUV").text
        song['song_title'] = song_title
    
    if soup.find(class_="ArtistSubtitle_subtitle__LaFIf") == None: 
        pass
    else:
        song_artist = soup.find(class_="ArtistSubtitle_subtitle__LaFIf").text
        song['song_artist'] = song_artist
    
    if soup.find(class_="SceneDescription_description__SDFKK") == None: 
        pass
    else:
        scene_description = soup.find(class_="SceneDescription_description__SDFKK").text
        song['scene_description'] = scene_description
            
    return song

In [ ]:
# shuffle datalist
shuffled = sorted(data, key=lambda L: random.random())
# gather third page info
i = 1
for episode_info in shuffled:
    if episode_info['link_episode'] == None:
        pass
    else:
    
        #Get page info
        req = requests.get(episode_info['link_episode'])
        soup = BeautifulSoup(req.text, "html.parser")
        full_page_3 = soup.find_all(class_="SongRow_container__TbgMq")
        print(f"{i}/{len(data)} Looking at {episode_info['link_episode']}")
        i += 1

        f=open('outputfile_def.json','a',encoding='utf-8')
        counter = 0
        #retrieve episode data
        for soup in full_page_3:  
            try:
                song_info = retrieve_song_page_info(soup)
                now = datetime.now()
                current_time = now.strftime("%H:%M:%S")
                current_date = now.strftime("%d/%m/%Y")
                counter = counter + 1

                writable_data = {'order': counter,
                                 'link_season': episode_info['link_season'],
                                 'date' : episode_info['date'],
                                 'season' : episode_info['season'],
                                 'title' : episode_info['title'],
                                 'episode' : episode_info['episode'],
                                 'releasedate_episode': episode_info['releasedate_episode'],
                                 'episode_description': episode_info['episode_description'],
                                 'song_title' : song_info['song_title'],
                                 'song_artist' : song_info['song_artist'],
                                 'scene_description' : song_info['scene_description'],
                                 'current_time' : current_time,
                                 'current_date' : current_date}
                sleep(2)
                print(song_info['song_title'])
                writable_json = json.dumps(writable_data)
                f.write(writable_json + '\n')

            except (KeyboardInterrupt, SystemExit):
                raise
            except:
                print("error")
                sleep(25)
                continue
        f.close()

1/106673 Looking at https://www.tunefind.com/show/fresh-meat/season-3/28758
2/106673 Looking at https://www.tunefind.com/show/rupauls-drag-race-all-stars/season-6/110847
Cover Girl
This is Our Country (Cast Version) [feat. The Cast of RuPaul's Drag Race All Stars, Season 6]
U Wear It Well
Stupid Love
Champion
Condragulations
I'm a Winner, Baby
3/106673 Looking at https://www.tunefind.com/show/the-only-way-is-essex/season-10/35667
4/106673 Looking at https://www.tunefind.com/show/ex-on-the-beach/season-7/50728
5/106673 Looking at https://www.tunefind.com/show/the-city/season-2/49700
6/106673 Looking at https://www.tunefind.com/show/wagon-train/season-5/107867
7/106673 Looking at https://www.tunefind.com/show/comedians-in-cars-getting-coffee/season-1/82800
8/106673 Looking at https://www.tunefind.com/show/sherlock-uk/season-1/11005
War
The Game Is On
A.S.A.P.
Uprising
Pink
Security Cameras
Pursuit
Which Bottle?
Opening Titles
9/106673 Looking at https://www.tunefind.com/show/making-the-c

70/106673 Looking at https://www.tunefind.com/show/comedians-in-cars-getting-coffee/season-10/82855
71/106673 Looking at https://www.tunefind.com/show/marvels-guardians-of-the-galaxy/season-2/53513
72/106673 Looking at https://www.tunefind.com/show/will-grace/season-4/52369
73/106673 Looking at https://www.tunefind.com/show/the-queen-of-flow/season-2/107135
74/106673 Looking at https://www.tunefind.com/show/made-in-chelsea/season-21/106462
75/106673 Looking at https://www.tunefind.com/show/young-sheldon/season-3/93602
Be Thou my vision
Do the Funky Chicken
76/106673 Looking at https://www.tunefind.com/show/the-tonight-show-starring-jimmy-fallon/season-2016/36971
Too Late for Goodbyes
Electric Avenue
Maggot Brain
77/106673 Looking at https://www.tunefind.com/show/the-kids-are-alright/season-1/73699
78/106673 Looking at https://www.tunefind.com/show/broad-city/season-2/21974
Doggy Wedding Drums
Speed Feeder
That's the Way
Golden Sun
79/106673 Looking at https://www.tunefind.com/show/ex-o

Buildings & Mountains
Keep Yourself Warm
140/106673 Looking at https://www.tunefind.com/show/tales-of-the-city/season-1/84515
Le Danse
Mi Dia Bonito (Remix)
All Because of You
You're Wrong
2oz Gin
Triangle (feat. Miny)
Daffodils
Primavera
141/106673 Looking at https://www.tunefind.com/show/american-ninja-warrior/season-14/225609
142/106673 Looking at https://www.tunefind.com/show/jane-the-virgin/season-5/79451
Let It Go
143/106673 Looking at https://www.tunefind.com/show/victorious/season-1/62288
WHOLE NIGHT TO PARTY
HOTRAGEOUS
Freak The Freak Out (feat. Victoria Justice)
Give It Up (feat. Elizabeth Gillies & Ariana Grande)
144/106673 Looking at https://www.tunefind.com/show/adventure-time/season-3/85033
On a Tropical Island (feat. John DiMaggio)
145/106673 Looking at https://www.tunefind.com/show/two-and-a-half-men/season-10/69771
146/106673 Looking at https://www.tunefind.com/show/grimm/season-6/40042
147/106673 Looking at https://www.tunefind.com/show/good-girls/season-4/109132
Dial

The Way of the Dodo (The Living Record)
210/106673 Looking at https://www.tunefind.com/show/i-am-frankie/season-1/74696
211/106673 Looking at https://www.tunefind.com/show/el-internado-las-cumbres/season-1/110182
212/106673 Looking at https://www.tunefind.com/show/the-simpsons/season-6/34604
213/106673 Looking at https://www.tunefind.com/show/the-goldbergs/season-4/46901
Dare
Bill Bailey, Won't You Please Come Home (feat. George Segal)
99 Luftballons
214/106673 Looking at https://www.tunefind.com/show/king-of-the-road/season-2/49989
215/106673 Looking at https://www.tunefind.com/show/the-next-step/season-6/67563
216/106673 Looking at https://www.tunefind.com/show/bones/season-4/76675
Fool For You
Ghost of a Chance
217/106673 Looking at https://www.tunefind.com/show/dancing-with-the-stars/season-8/35932
218/106673 Looking at https://www.tunefind.com/show/happy-endings/season-3/13504
Take On Me
219/106673 Looking at https://www.tunefind.com/show/a-business-proposal/season-1/220311
Meltin

274/106673 Looking at https://www.tunefind.com/show/hard-knocks/season-1/51660
275/106673 Looking at https://www.tunefind.com/show/kims-convenience/season-3/75393
276/106673 Looking at https://www.tunefind.com/show/the-ellen-degeneres-show/season-2018/63048
277/106673 Looking at https://www.tunefind.com/show/the-expanse/season-4/93864
278/106673 Looking at https://www.tunefind.com/show/manhattan/season-2/26069
Blind Barnabas
Ain't You Shamed
279/106673 Looking at https://www.tunefind.com/show/doubt/season-1/49853
Got the Yeah
Wait For You
Control
280/106673 Looking at https://www.tunefind.com/show/drop-dead-diva/season-5/15336
Who You Are
281/106673 Looking at https://www.tunefind.com/show/americas-got-talent/season-10/33319
Fame
282/106673 Looking at https://www.tunefind.com/show/rebel/season-1/47517
283/106673 Looking at https://www.tunefind.com/show/dancing-with-the-stars/season-6/35885
284/106673 Looking at https://www.tunefind.com/show/prime-suspect/season-1/9680
Howlin' for You
T

...

Hesitate
12689/106673 Looking at https://www.tunefind.com/show/rescue-me/season-3/2459
12690/106673 Looking at https://www.tunefind.com/show/in-the-dark-2019/season-2/98799
Blood Red Sentimental Blues
12691/106673 Looking at https://www.tunefind.com/show/luther-uk/season-1/8854
Mad World
Mad World
Don't You Want Me
Everybody's Got to Learn Sometime
12692/106673 Looking at https://www.tunefind.com/show/the-simpsons/season-31/96407
Amazing Grace
First Part of the Rising Organ Cheer
12693/106673 Looking at https://www.tunefind.com/show/selling-sunset/season-1/80293
I'm The Real Thing
Next Level
Just Watch Me Now
Going Harder
Shotgun
Wildfire
Green Light
One Life
Like This, Like That
My Way
Cut Your Teeth (Kygo Remix)
No Love
Third Eye
Main Attraction (feat. Kool G Rap)
12694/106673 Looking at https://www.tunefind.com/show/heroes/season-1/2164
I'm Confessin'
12695/106673 Looking at https://www.tunefind.com/show/sabrina-the-teenage-witch/season-6/66625
12696/106673 Looking at https://www.tu

Last Last
12750/106673 Looking at https://www.tunefind.com/show/damien/season-1/29981
Nocturne for Piano in C Sharp Minor, KK Anh. Ia, No. 6
12751/106673 Looking at https://www.tunefind.com/show/chicago-fire/season-1/14224
12752/106673 Looking at https://www.tunefind.com/show/abyss/season-1/90482
12753/106673 Looking at https://www.tunefind.com/show/ambitions/season-1/85466
Lights On
Belong to You
Indiansong
12754/106673 Looking at https://www.tunefind.com/show/colony/season-3/63463
12755/106673 Looking at https://www.tunefind.com/show/two-and-a-half-men/season-11/69789
12756/106673 Looking at https://www.tunefind.com/show/doogie-kamealoha-md/season-1/112775
12757/106673 Looking at https://www.tunefind.com/show/will-grace/season-8/52473
12758/106673 Looking at https://www.tunefind.com/show/walker/season-1/105069
Kinda Shaken
Hangin' On
I Gotta Cry
Magnolia
Say What You Mean
Warm
Summer Begs
Calling It
12759/106673 Looking at https://www.tunefind.com/show/claws/season-2/64417
I'm Every 

12811/106673 Looking at https://www.tunefind.com/show/the-office-us/season-7/17728
12812/106673 Looking at https://www.tunefind.com/show/hollyoaks/season-11/43601
12813/106673 Looking at https://www.tunefind.com/show/our-cartoon-president/season-2/103958
12814/106673 Looking at https://www.tunefind.com/show/the-bureau-of-magical-things/season-2/225132
12815/106673 Looking at https://www.tunefind.com/show/the-closer/season-7/50179
12816/106673 Looking at https://www.tunefind.com/show/the-office-us/season-9/17785
12817/106673 Looking at https://www.tunefind.com/show/the-goldbergs/season-8/104936
9 To 5
12818/106673 Looking at https://www.tunefind.com/show/wentworth/season-6/65004
We Grow
12819/106673 Looking at https://www.tunefind.com/show/roswell/season-1/21485
Delirium
Blown Away
Quicksand
Time Served
Get You In the Morning
Loves Deadly Touch
Snakecharmer
The Le Tingo
12820/106673 Looking at https://www.tunefind.com/show/seal-team/season-1/55433
Sunrise: Season 1 (feat. Joel Virgel)
H

12876/106673 Looking at https://www.tunefind.com/show/biggest-loser/season-8/34213
12877/106673 Looking at https://www.tunefind.com/show/castle-rock/season-1/67626
Death Don't Have No Mercy
Twenty-Four Hours From Tulsa
12878/106673 Looking at https://www.tunefind.com/show/the-tonight-show-starring-jimmy-fallon/season-2022/222221
Perfect Harmony
Living All Alone
Toca Tuesday Freestyle
Age of Anxiety II (Rabbit Hole)
The Imperial (feat. Action Bronson, Royce Da 5' 9" & Black Thought)
12879/106673 Looking at https://www.tunefind.com/show/the-wonder-years/season-4/48163
Teach Your Children
Third Man Theme
12880/106673 Looking at https://www.tunefind.com/show/maxxx/season-2/101830
12881/106673 Looking at https://www.tunefind.com/show/last-man-standing/season-6/83635
12882/106673 Looking at https://www.tunefind.com/show/heroes/season-1/2161
Eyes
Jatt Ho Giya Sharabee
The Way She's Moving
12883/106673 Looking at https://www.tunefind.com/show/ncis/season-1/6088
12884/106673 Looking at https://

12937/106673 Looking at https://www.tunefind.com/show/south-park/season-6/25744
12938/106673 Looking at https://www.tunefind.com/show/bull/season-4/95503
Asleep (feat. Anna Wise)
12939/106673 Looking at https://www.tunefind.com/show/angel/season-1/5771
12940/106673 Looking at https://www.tunefind.com/show/american-dad/season-3/35059
(You Can Still) Rock In America
12941/106673 Looking at https://www.tunefind.com/show/boardwalk-empire/season-4/15936
It Had To Be You (feat. Vince Giordano & The Nighthawks)
Jazzin' Baby Blues
CMP12964 Calliope Time
Plaisir d'Amour SON SAS 0027 02801
That's a Lot of Bunk
Malinda Brown
PCLm122.21 Scherzo No. 1 in B flat Major, Op. posth. D593
If I Lose, Let Me Lose (Mama Don't Mind)
Manda
Dixie (I Wish I Was In)
Down By Jungle Town
April Smiles Waltz Sourire d'Avril, Op. 11
I'm Through With You
I'm A Little Blackbird
Farewell Daddy Blues
Don't Mind the Rain
If You Want the Rainbow (You Must Have the Rain) [feat. Vince Giordano & The Nighthawks]
12942/106673

In [ ]:
# print to csv
#df = pd.DataFrame(all_data)
#df.to_csv('tunefind_final.csv', sep=";")